# Layer-specific fMRI processing pipeline: functional processing & pRF mapping

It is assumed that this workflow is run following the laminar-fMRI-pipeline-advanced-skullstrip workflow.

The functional processing pipeline aims to follow the steps followed in fMRIPrep, adapted for partial FoV fMRI data. Reasons for not using fMRIPrep directly:  
- from fMRIPrep website: a reason not to use fMRIPrep is very narrow FoV images, which often do not contain enough information for standard image registration methods to work correctly
- fMRIPrep is designed to take a T1 MPRAGE image as input, not MP2RAGE
- pRF mapping can be carried out in native space - here we avoid additional data perturbations by keeping the data in native space

The pipeline uses the anatomical surface reconstruction from the laminar-fMRI-pipeline-advanced-skullstrip workflow as input. The steps implemented in the pipeline are as follows:
- discard initial fMRI volumes to allow for T1 equilibration
- realignment: head-motion estimation and correction (FSL MCFLIRT); within and between sessions
- (optional) susceptibility-derived distortion estimation and unwarping (AFNI 3dqwarp)
- (optional) slice-timing correction (AFNI 3dTshift)
- compute temporal SNR (to assess the noisiness of the data in different brain areas)
- co-registration of functional and structural data (FreeSurfer bbregister, FLIRT FSL) - note: structural data is brought into functional space to avoid superfluous interpolation of functional volumes!
- iteratively: check results (and manual correction) w/ tkregisterfv and run bbregister again
- surface sampling (FreeSurfer mri_vol2surf)
- confounds (FSL fsl_motion_outliers then fsl_regfilt?)
- detection of non-steady states ???

pRF: decide on software
- what format of input data?
- what format of aperture parameters?
- anatomical priors (neuropythy)
- combine empirical estimate and anatomical priors for Bayesian
- decide which sessions to use (pol, ecc, bar)


try using raw image (not skull-stripped) for coreg

### Set preferences
Whether or not to write the workflow viz graph, run pipeline, run specific branches of workflow...

In [1]:
# whether or not to run the pipeline
run_pipeline = True   

# whether or not to write workflow graph (svg)
write_graph  = True                           
                        
# whether manual edits exist (for coregistration)
manual_edits = True      

# whether to do unwarping
unwarp = False                                

# coregistration method: 'flirt','freesurfer', 'antsRegistration' or 'itk-snap'
coreg_method = 'antsRegistration' 

# coregistration direction: either from functional to structural ('func2struct') or vice versa ('struct2func')
coreg_dir = 'struct2func'

# number of cores to use: either set explicitly or based on settings in batch file
import os
#n_procs = 1
n_procs = int(os.getenv('OMP_NUM_THREADS'))   
print(n_procs)

20


### Set paths
All computer-dependent paths

In [2]:
from os.path import join as opj

doc_dir = '/home/mayaaj90/'
data_dir = '/scratch/mayaaj90/7T-ret/'

# general software directory
software_dir = opj(doc_dir,'programs')

# SPM dir
spm_dir = opj(software_dir,'spm12')

# data directory
raw_data_dir = opj(data_dir,'raw')

# scripts directory
der_dir = opj(data_dir,'derivatives')

# dicoms directory
dicom_dir = opj(data_dir,'dicoms')

# location of freesurfer skull-stripped T1 (output of structural processing pipeline)
struct_out = opj(data_dir,'output','freesurfer_externalbrainmask')

# output directory for datasink
out_dir = opj(data_dir,'output')

### Imports
Import required libraries, set paths

In [3]:
import re

from nipype.interfaces.io import DataGrabber, DataSink

from nipype import Node, MapNode, JoinNode, Workflow

from nipype.interfaces.freesurfer import MRIConvert

#import nipype_settings
import nipype.interfaces.matlab as Matlab
from nipype.interfaces.base import (
    CommandLineInputSpec,
    CommandLine,
    TraitedSpec,
    BaseInterface, 
    BaseInterfaceInputSpec, 
    File,
    Directory
)

from string import Template

from nipype.interfaces.utility import Function, IdentityInterface, Merge, Select
from nipype.interfaces.base import BaseInterface, BaseInterfaceInputSpec, CommandLine, Directory, File, TraitedSpec, traits

from nipype import config
config.enable_debug_mode()

from os.path import abspath

from nipype.interfaces.freesurfer.model import Binarize

import pygraphviz 

from pydicom.data import get_testdata_file
from pydicom import dcmread

from nipype.interfaces.fsl import BET, PrepareFieldmap, ExtractROI, MCFLIRT, Merge, ConvertXFM, FLIRT

from nipype.interfaces.freesurfer.registration import MRICoreg
from nipype.interfaces.freesurfer.preprocess import BBRegister

from nipype.interfaces.dcmstack import MergeNifti

import sys
sys.path.append(software_dir)
from ApplyXfm4D import ApplyXfm4D

from nipype.interfaces.fsl.preprocess import FUGUE

from nipype.interfaces.afni import Warp, TShift

from nipype.interfaces.spm import SliceTiming

import neuropythy as ny

import nipype.interfaces.matlab as Matlab

from nipype.interfaces.ants.registration import Registration
from nipype.interfaces.ants import N4BiasFieldCorrection
from nipype.interfaces.ants import ApplyTransforms

from nipype.interfaces.fsl.maths import BinaryMaths

# set SPM path
os.environ['SPM_PATH']=spm_dir

from nipype.interfaces import spm
spm.SPMCommand.set_mlab_paths(paths=spm_dir)
#print(spm.Info.name())
#print(spm.SPMCommand().version)

220530-20:26:33,816 nipype.utils WARNING:
	 A newer version (1.8.1) of nipy/nipype is available. You are using 1.7.1


ModuleNotFoundError: No module named 'numpy.core._multiarray_umath'

220530-20:26:46,367 nipype.interface DEBUG:
	 matlab command or path has changed. recomputing version.
220530-20:26:46,494 nipype.interface DEBUG:
	 nodesktop_True
220530-20:26:46,495 nipype.interface DEBUG:
	 nosplash_True
220530-20:26:46,495 nipype.interface DEBUG:
	 single_comp_thread_True
220530-20:26:46,496 nipype.interface DEBUG:
	 nodesktop_True
220530-20:26:46,496 nipype.interface DEBUG:
	 nosplash_True
220530-20:26:46,496 nipype.interface DEBUG:
	 single_comp_thread_True


In [4]:
#test = Node(Registration(),name='test')

### Neuropythy configuration
On startup, neuropythy looks for file ~/.npythyrc. Here, we override these settings and environment variables

### Specify important variables

In [5]:
wf_name = 'wf_laminar_fMRI_func_pRF'

UNI_id = 'UNI.nii'                                              # name of raw T1 UNI image
T1_id = 'T1.mgz'                                                # name of preprocessed T1 (output of structural processing pipeline)
brainmask_id = 'brainmask.nii'
GM_id = 'gm.mask_thresh.nii'
WM_id = 'wm.mask_thresh.nii'

# manual correction files - from itksnap
occipital_id = 'occipital.nii.gz'
coregT1_out_id = 'coregT1_out.nii'
coreg_itksnap_struct2func_txt_id = 'coreg_itksnap_struct2func.txt'
coreg_itksnap_struct2func_mat_id = 'coreg_itksnap_struct2func.mat'
coreg_itksnap_func2struct_txt_id = 'coreg_itksnap_func2struct.txt'
coreg_itksnap_func2struct_mat_id = 'coreg_itksnap_func2struct.mat'


fmap_magnitude1_id = 'magnitude1.nii'
fmap_magnitude2_id = 'magnitude2.nii'
fmap_phasediff_id = 'phasediff.nii'

n_dummy = 4                                                     # number of dummy scans to discard to allow for T1 equilibration

n_vol_bar1 = 124                                                # number of volumes of bar pRF mapping stimulus
n_vol_bar2 = n_vol_bar1                                         # number of volumes of bar pRF mapping stimulus
n_vol_ecc1 = 131                                                # number of volumes of ecc pRF mapping stimulus
n_vol_ecc2 = n_vol_ecc1                                         # number of volumes of ecc pRF mapping stimulus
n_vol_pol1 = 254                                                # number of volumes of pol pRF mapping stimulus
n_vol_pol2 = n_vol_pol1                                         # number of volumes of pol pRF mapping stimulus
n_vol_rs_ge = 50                                                # number of volumes of GE RS pRF mapping stimulus
n_vol_rs_se = 50                                                # number of volumes of SE RS pRF mapping stimulus

# iterables
subject_list = ['sub-01']#,'sub-02']#,'sub-03']                 # subject identifiers
sess_id_list = ['task-bar_run-01', 'task-bar_run-02',           # func session identifiers
             'task-pol_run-01', 'task-pol_run-02',
             'task-ecc_run-01', 'task-ecc_run-02',
             'rest_run-01']#, 'rest_run-02']
sess_nvol_list = [n_vol_bar1, n_vol_bar2,
                  n_vol_pol1, n_vol_pol2,
                  n_vol_ecc1, n_vol_ecc2,
                  n_vol_rs_ge]#, n_vol_rs_se]
sess_nr_list = list(range(0, len(sess_id_list)))

Get TR/TE/slice timing info from DICOM of sub-01

Future improvement: don't hard-code this 

In [6]:
fpath = opj(dicom_dir,'sub-01','MR bar_cmrr_mbep2d_bold_0p8_fov148_iPAT3_68_50sli_TR3000','MR000000.dcm')
dc = dcmread(fpath)

print(dc)

Dataset.file_meta -------------------------------
(0002, 0000) File Meta Information Group Length  UL: 196
(0002, 0001) File Meta Information Version       OB: b'\x00\x01'
(0002, 0002) Media Storage SOP Class UID         UI: MR Image Storage
(0002, 0003) Media Storage SOP Instance UID      UI: 1.3.12.2.1107.5.2.34.18919.2019102111005792386547056
(0002, 0010) Transfer Syntax UID                 UI: Explicit VR Little Endian
(0002, 0012) Implementation Class UID            UI: 1.2.276.0.7230010.3.0.3.6.2
(0002, 0013) Implementation Version Name         SH: 'OFFIS_DCMTK_362'
-------------------------------------------------
(0008, 0005) Specific Character Set              CS: 'ISO_IR 100'
(0008, 0008) Image Type                          CS: ['ORIGINAL', 'PRIMARY', 'M', 'ND', 'MOSAIC']
(0008, 0012) Instance Creation Date              DA: '20191021'
(0008, 0013) Instance Creation Time              TM: '110058.109000'
(0008, 0016) SOP Class UID                       UI: MR Image Storage
(000

In [7]:
# repetition time
TR = dc.RepetitionTime / 1000                               # in seconds [s]
TR_str = '%.1fs' % TR

# echo time
TE = dc.EchoTime / 1000                                     # in seconds [s]

# MR acquisition type
acquisition_type = dc.MRAcquisitionType

# slice acquisition times
slice_timing = dc[0x0019, 0x1029].value                      # in milliseconds [ms]
slice_timing[:] = [x / 1000 for x in slice_timing]            # in seconds [s]

# number of slices
num_slices = dc[0x0019, 0x100a].value

# time of volume acquisition
TA = TR-(TR/num_slices)

In [8]:
TR

3.0

Get parameters needed for fieldmap correction (see: https://lcni.uoregon.edu/kb-articles/kb-0003)

In [9]:
# effective echo spacing 
bandwidth_per_pixel_phase_encode = dc[0x0019, 0x1028].value
acquisition_matrix_text = dc[0x0051, 0x100b].value
matrix_size_phase = float(re.search(r'\d+', acquisition_matrix_text).group())
                                    # NOTE: The size of the image in the phase direction 
                                    # is *usually* the first number in the field (0051, 100b), 
                                    # AcquisitionMatrixText. This is, however, not always the 
                                    # case, so it is better to determine the actual size 
                                    # (rows or columns) of your reconstructed image in the 
                                    # phase encode direction. You can also just read the 
                                    # effective echo spacing from the Series Info screen 
                                    # in MRIConvert if you are running the latest version.
effective_echo_spacing = 1/(bandwidth_per_pixel_phase_encode + matrix_size_phase)

# total readout time for an EPI sequence
total_readout_time = (matrix_size_phase - 1) * effective_echo_spacing

# deltaTE
delta_TE = 2.46                      # in milliseconds [ms]      
                                     # (a float, nipype default value: 2.46) 
                                     # echo time difference of the fieldmap 
                                     # sequence in ms. (usually 2.46ms in Siemens)

### Create workflow
About connecting nodes: https://nipype.readthedocs.io/en/0.11.0/users/joinnode_and_itersource.html

In [10]:
wf = Workflow(name=wf_name, base_dir=der_dir)

### Subjects & functional sessions

In [11]:
subjects = Node(IdentityInterface(fields=['subject_id']),name='subjects')
subjects.iterables = [('subject_id', subject_list)]

In [12]:
sessions = Node(IdentityInterface(fields=['sess_id','sess_nvol','sess_nr']),name='sessions')
sessions.iterables = [('sess_id', sess_id_list), ('sess_nvol', sess_nvol_list), ('sess_nr', sess_nr_list)]
sessions.synchronize = True

### Acquisition parameters

In [13]:
acquisitionParams = Node(IdentityInterface(fields=['n_dummy', 'TR'
                                                  'TA','TR_str','TE','acquisition_type',
                                                  'slice_timing','num_slices',
                                                  'effective_echo_spacing','total_readout_time',
                                                  'delta_TE']),
                         name='acquisitionParams')

acquisitionParams.inputs.n_dummy = n_dummy
acquisitionParams.inputs.TR = TR
acquisitionParams.inputs.TA = TA
acquisitionParams.inputs.TR_str = TR_str
acquisitionParams.inputs.TE = TE
acquisitionParams.inputs.acquisition_type = acquisition_type
acquisitionParams.inputs.slice_timing = slice_timing
acquisitionParams.inputs.num_slices = num_slices
acquisitionParams.inputs.effective_echo_spacing = effective_echo_spacing
acquisitionParams.inputs.total_readout_time = total_readout_time
acquisitionParams.inputs.delta_TE = delta_TE

### Grab data

DataGrabber is an interface for collecting files from hard drive. It is very flexible and supports almost any file organization of your data you can imagine.
<br>More info: https://nipype.readthedocs.io/en/0.11.0/users/grabbing_and_sinking.html

#### Anatomical and field map data

In [14]:
datasource = Node(DataGrabber(infields=['subject_id'], outfields=['UNI', 'T1', 'brainmask', 'GM', 'WM',
                                                                  'fmap_magnitude1', 
                                                                  'fmap_magnitude2',
                                                                  'fmap_phasediff', 
                                                                  'subject_id']),
                 name='datasource')
datasource.inputs.base_directory = data_dir
datasource.inputs.sort_filelist = False
datasource.inputs.template = '*'
datasource.inputs.field_template = dict(UNI='raw/%s/anat/'+UNI_id,
                                        T1='output/freesurfer_externalbrainmask/_subject_id_%s/'+T1_id,
                                        brainmask='output/freesurfer_externalbrainmask/_subject_id_%s/'+brainmask_id,
                                        GM='output/freesurfer_externalbrainmask/_subject_id_%s/'+GM_id,
                                        WM='output/freesurfer_externalbrainmask/_subject_id_%s/'+WM_id,
                                        fmap_magnitude1='raw/%s/fmap/'+fmap_magnitude1_id,
                                        fmap_magnitude2='raw/%s/fmap/'+fmap_magnitude2_id,
                                        fmap_phasediff='raw/%s/fmap/'+fmap_phasediff_id
                                       )
datasource.inputs.template_args = dict(UNI=[['subject_id']],
                                       T1=[['subject_id']],
                                       brainmask=[['subject_id']],
                                       GM=[['subject_id']],
                                       WM=[['subject_id']],
                                       fmap_magnitude1=[['subject_id']],
                                       fmap_magnitude2=[['subject_id']],
                                       fmap_phasediff=[['subject_id']]
                                       )

In [15]:
wf.connect([(subjects, datasource,[('subject_id', 'subject_id')])])

220530-20:27:17,843 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.datasource): No edge data
220530-20:27:17,844 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.datasource): new edge data: {'connect': [('subject_id', 'subject_id')]}


##### Convert T1.mgz to .nii

In [16]:
out_type = 'nii'

In [17]:
convertT1ToNii = Node(MRIConvert(out_type=out_type), name='convertT1ToNii')

In [18]:
wf.connect([(datasource,convertT1ToNii,[('T1', 'in_file')])])

220530-20:27:17,862 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.convertT1ToNii): No edge data
220530-20:27:17,863 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.convertT1ToNii): new edge data: {'connect': [('T1', 'in_file')]}


#### Functional data

In [19]:
datasourceFunc = Node(DataGrabber(infields=['subject_id','sess_id'], outfields=['sess_id', 
                                                                  'subject_id']),
                 name='datasourceFunc')
datasourceFunc.inputs.base_directory = data_dir
datasourceFunc.inputs.sort_filelist = False
datasourceFunc.inputs.template = '*'
datasourceFunc.inputs.field_template = dict(sess_id='raw/%s/func/%s.nii'
                                       )
datasourceFunc.inputs.template_args = dict(sess_id=[['subject_id','sess_id']]
                                       )

In [20]:
wf.connect([(subjects, datasourceFunc, [('subject_id', 'subject_id')])])
wf.connect([(sessions, datasourceFunc, [('sess_id', 'sess_id')])])

220530-20:27:17,878 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.datasourceFunc): No edge data
220530-20:27:17,878 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.datasourceFunc): new edge data: {'connect': [('subject_id', 'subject_id')]}
220530-20:27:17,879 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.datasourceFunc): No edge data
220530-20:27:17,879 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.datasourceFunc): new edge data: {'connect': [('sess_id', 'sess_id')]}


#### Manual edits
(if they exist)

In [21]:
datasourceManualEdits = Node(DataGrabber(infields=['subject_id'], outfields=['coreg_itksnap_struct2func_txt',
                                                                             'coreg_itksnap_struct2func_mat',
                                                                             'coreg_itksnap_func2struct_txt',
                                                                             'coreg_itksnap_func2struct_mat',
                                                                             'coreg_itksnap_T1',
                                                                             'occipital',
                                                                             'subject_id']),
                 name='datasourceManualEdits')
datasourceManualEdits.inputs.base_directory = data_dir
datasourceManualEdits.inputs.sort_filelist = False
datasourceManualEdits.inputs.template = '*'
datasourceManualEdits.inputs.field_template = dict(coreg_itksnap_struct2func_txt='manualcorr/%s/'+coreg_itksnap_struct2func_txt_id,
                                                   coreg_itksnap_struct2func_mat='manualcorr/%s/'+coreg_itksnap_struct2func_mat_id,
                                                   coreg_itksnap_func2struct_txt='manualcorr/%s/'+coreg_itksnap_func2struct_txt_id,
                                                   coreg_itksnap_func2struct_mat='manualcorr/%s/'+coreg_itksnap_func2struct_mat_id,
                                                   coreg_itksnap_T1='manualcorr/%s/'+coregT1_out_id,
                                                   occipital='manualcorr/%s/'+occipital_id
                                       )
datasourceManualEdits.inputs.template_args = dict(coreg_itksnap_struct2func_txt=[['subject_id']],
                                                  coreg_itksnap_struct2func_mat=[['subject_id']],
                                                  coreg_itksnap_func2struct_txt=[['subject_id']],
                                                  coreg_itksnap_func2struct_mat=[['subject_id']],
                                                  coreg_itksnap_T1=[['subject_id']],
                                                  occipital=[['subject_id']]
                                       )

In [22]:
if manual_edits: 
    wf.connect([(subjects, datasourceManualEdits, [('subject_id', 'subject_id')])])

220530-20:27:17,897 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.datasourceManualEdits): No edge data
220530-20:27:17,898 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.datasourceManualEdits): new edge data: {'connect': [('subject_id', 'subject_id')]}


### Calculate field map

Using fsl_prepare_fieldmap. 

"If you have data from a SIEMENS scanner then we strongly recommend that the tool fsl_prepare_fieldmap is used to generate the required input data for FEAT or fugue. Fieldmap data from a SIEMENS scanner takes the form of one phase difference image and two magnitude images (one for each echo time). In the following, where a magnitude image is required, pick the "best looking" one. This image is used for registration and masking but the process is not particularly sensitive to the quality and typically either image will work fine.

Brain extraction of the magnitude image is very important and must be tight - that is, it must exclude all non-brain voxels and any voxels with only a small partial volume contribution. The reason for this is that these areas are normally very noisy in the phase image (look at them in FSLView - if they are not noisy then this is not so important). It is crucial that the mask (derived from this brain extracted image) contains few of these noisy voxels. This is most easily done by making the brain extraction very tight, erring on excluding brain voxels. The exclusion of brain voxels in this instance is actually fine and will have no repercussions, since the fieldmap is extrapolated beyond this mask, and that is the only purpose that the mask plays. Therefore make sure your mask is (if it can't be perfect) too small. As noted above, either magnitude image (from the different echos) can normally be used here - it is not that important." 

Source: https://fsl.fmrib.ox.ac.uk/fsl/fslwiki/FUGUE/Guide#SIEMENS_data

#### Brain extract magnitude image
Use magnitude1.nii by default

In [23]:
# FSL BET - run on magnitude1.nii image
betMagnImg = Node(BET(),name='betMagnImg')

220530-20:27:17,905 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [24]:
wf.connect([(datasource,betMagnImg,[('fmap_magnitude1','in_file')])])

220530-20:27:17,912 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.betMagnImg): No edge data
220530-20:27:17,913 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.betMagnImg): new edge data: {'connect': [('fmap_magnitude1', 'in_file')]}


#### Prepare field map

Prepares a fieldmap suitable for FEAT from SIEMENS data - saves output in rad/s format (e.g. `fsl_prepare_fieldmap SIEMENS images_3_gre_field_mapping images_4_gre_field_mapping fmap_rads 2.65`).


[Mandatory]
delta_TE: (a float, nipype default value: 2.46)
        echo time difference of the fieldmap sequence in ms. (usually 2.46ms
        in Siemens)
        flag: %f, position: -2
in_magnitude: (an existing file name)
        Magnitude difference map, brain extracted
        flag: %s, position: 3
in_phase: (an existing file name)
        Phase difference map, in SIEMENS format range from 0-4096 or 0-8192)
        flag: %s, position: 2
        
        
https://nipype.readthedocs.io/en/0.12.1/interfaces/generated/nipype.interfaces.fsl.epi.html#preparefieldmap

In [25]:
prepFieldMap = Node(PrepareFieldmap(), name='prepFieldMap')

220530-20:27:17,920 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [26]:
wf.connect([(acquisitionParams,prepFieldMap,[('delta_TE','delta_TE')])])
wf.connect([(betMagnImg,prepFieldMap,[('out_file','in_magnitude')])])
wf.connect([(datasource,prepFieldMap,[('fmap_phasediff','in_phase')])])

220530-20:27:17,928 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.acquisitionParams, wf_laminar_fMRI_func_pRF.prepFieldMap): No edge data
220530-20:27:17,929 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.acquisitionParams, wf_laminar_fMRI_func_pRF.prepFieldMap): new edge data: {'connect': [('delta_TE', 'delta_TE')]}
220530-20:27:17,929 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.betMagnImg, wf_laminar_fMRI_func_pRF.prepFieldMap): No edge data
220530-20:27:17,930 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.betMagnImg, wf_laminar_fMRI_func_pRF.prepFieldMap): new edge data: {'connect': [('out_file', 'in_magnitude')]}
220530-20:27:17,930 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.prepFieldMap): No edge data
220530-20:27:17,930 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.prepFieldMap): new edge data: {'connect': [('fmap_phasediff', 'in_phase')]}


### Discard initial fMRI volumes to allow for T1 equilibration


In [27]:
discardDummies = Node(ExtractROI(t_min=n_dummy), name='discardDummies')

220530-20:27:17,938 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [28]:
wf.connect([(datasourceFunc, discardDummies,[('sess_id', 'in_file')])])
wf.connect([(sessions, discardDummies,[('sess_nvol', 't_size')])])

220530-20:27:17,943 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasourceFunc, wf_laminar_fMRI_func_pRF.discardDummies): No edge data
220530-20:27:17,944 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasourceFunc, wf_laminar_fMRI_func_pRF.discardDummies): new edge data: {'connect': [('sess_id', 'in_file')]}
220530-20:27:17,944 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.discardDummies): No edge data
220530-20:27:17,945 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.discardDummies): new edge data: {'connect': [('sess_nvol', 't_size')]}


### Realignment: head-motion estimation and correction (FSL MCFLIRT)
https://fsl.fmrib.ox.ac.uk/fsl/fslwiki/MCFLIRT

https://nipype.readthedocs.io/en/0.12.1/interfaces/generated/nipype.interfaces.fsl.preprocess.html

citation: Jenkinson, M., Bannister, P., Brady, J. M. and Smith, S. M. Improved Optimisation for the Robust and Accurate Linear Registration and Motion Correction of Brain Images. NeuroImage, 17(2), 825-841, 2002. 

First, motion-correction with MCFLIRT, within each session, saving the resulting transformation matrices. Then, concatenate the mean runs from each session and realign to each other with MCFLIRT, saving the transformation matrices. Loop through each matrix in the MCFLIRT output and do 'convert_xfm -omat CONCAT_0000 -concat reg_series1_to_series2.mat MAT_0000' for all MAT* files, then use applyxfm4D, with the "-userprefix CONCAT_" option. This does all transformations at once, directly from the original data and minimizes interpolation effects. Based on: https://www.jiscmail.ac.uk/cgi-bin/webadmin?A2=fsl;21c97ca8.06

#### Within sessions

In [29]:
mean_vol = True             # (a boolean) register to mean volume
save_mats = True             # (a boolean) save transformation parameters

In [30]:
mcflirtWithinSess = Node(MCFLIRT(mean_vol = mean_vol, save_mats=save_mats), 
               name='mcflirtWithinSess')

220530-20:27:17,957 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [31]:
wf.connect([(discardDummies, mcflirtWithinSess,[('roi_file','in_file')])])

220530-20:27:17,964 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.discardDummies, wf_laminar_fMRI_func_pRF.mcflirtWithinSess): No edge data
220530-20:27:17,964 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.discardDummies, wf_laminar_fMRI_func_pRF.mcflirtWithinSess): new edge data: {'connect': [('roi_file', 'in_file')]}


In [32]:
#fsl.MCFLIRT.help()

#### Between sessions
##### Concatenate mean runs

In [33]:
dimension = 't'
output_type = 'NIFTI'
merged_file = 'merged_means.nii'

In [34]:
concatenateMeans = JoinNode(Merge(dimension=dimension, output_type=output_type, merged_file=merged_file),
                        joinfield='in_files',
                        joinsource='sessions',
                        name="concatenateMeans")

220530-20:27:17,983 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
220530-20:27:17,984 nipype.workflow DEBUG:
	 Converted the join node concatenateMeans field in_files trait type from a legal value to a pathlike object or string representing an existing file


In [35]:
wf.connect([(mcflirtWithinSess, concatenateMeans,[('mean_img', 'in_files')])])

220530-20:27:17,990 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.mcflirtWithinSess, wf_laminar_fMRI_func_pRF.concatenateMeans): No edge data
220530-20:27:17,991 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.mcflirtWithinSess, wf_laminar_fMRI_func_pRF.concatenateMeans): new edge data: {'connect': [('mean_img', 'in_files')]}


##### MCFLIRT on merged mean runs

In [36]:
mean_vol = True               # (a boolean) register to mean volume
save_mats = True               # (a boolean) save transformation parameters

In [37]:
mcflirtBetweenSess = Node(MCFLIRT(mean_vol = mean_vol, save_mats=save_mats), 
               name='mcflirtBetweenSess')

220530-20:27:18,3 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [38]:
wf.connect([(concatenateMeans, mcflirtBetweenSess,[('merged_file','in_file')])])

220530-20:27:18,10 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.concatenateMeans, wf_laminar_fMRI_func_pRF.mcflirtBetweenSess): No edge data
220530-20:27:18,11 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.concatenateMeans, wf_laminar_fMRI_func_pRF.mcflirtBetweenSess): new edge data: {'connect': [('merged_file', 'in_file')]}


In [39]:
MCFLIRT.help()

Wraps the executable command ``mcflirt``.

FSL MCFLIRT wrapper for within-modality motion correction

For complete details, see the `MCFLIRT Documentation.
<https://fsl.fmrib.ox.ac.uk/fsl/fslwiki/MCFLIRT>`_

Examples
--------
>>> from nipype.interfaces import fsl
>>> mcflt = fsl.MCFLIRT()
>>> mcflt.inputs.in_file = 'functional.nii'
>>> mcflt.inputs.cost = 'mutualinfo'
>>> mcflt.inputs.out_file = 'moco.nii'
>>> mcflt.cmdline
'mcflirt -in functional.nii -cost mutualinfo -out moco.nii'
>>> res = mcflt.run()  # doctest: +SKIP

Inputs::

        [Mandatory]
        in_file: (a pathlike object or string representing an existing file)
                timeseries to motion-correct
                argument: ``-in %s``, position: 0

        [Optional]
        out_file: (a pathlike object or string representing a file)
                file to write
                argument: ``-out %s``
        cost: ('mutualinfo' or 'woods' or 'corratio' or 'normcorr' or
                  'normmi' or 'leastsquares

##### Concatenate transformation matrices


Select given session's transformation mat

In [40]:
betweenMat = Node(Select(), name='betweenMat')

In [41]:
wf.connect([(mcflirtBetweenSess, betweenMat, [('mat_file', 'inlist')])])
wf.connect([(sessions, betweenMat, [('sess_nr', 'index')])])

220530-20:27:18,34 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.mcflirtBetweenSess, wf_laminar_fMRI_func_pRF.betweenMat): No edge data
220530-20:27:18,35 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.mcflirtBetweenSess, wf_laminar_fMRI_func_pRF.betweenMat): new edge data: {'connect': [('mat_file', 'inlist')]}
220530-20:27:18,35 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.betweenMat): No edge data
220530-20:27:18,36 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.betweenMat): new edge data: {'connect': [('sess_nr', 'index')]}


Concatenate within-session mat_files with corresponding session's between-session realignment mat_file

In [42]:
concat_xfm = True         # (a boolean) write joint transformation of two input matrices
                          # flag: -concat, position: -3
                          # mutually_exclusive: invert_xfm, concat_xfm, fix_scale_skew
                          # requires: in_file2

In [43]:
concatenateTransforms = MapNode(ConvertXFM(concat_xfm=concat_xfm),
                            name = 'concatenateTransforms', iterfield=['in_file2'])

220530-20:27:18,48 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
220530-20:27:18,50 nipype.workflow DEBUG:
	 adding multipath trait: in_file2


In [44]:
wf.connect([(betweenMat,concatenateTransforms,[('out','in_file')])])
wf.connect([(mcflirtWithinSess,concatenateTransforms,[('mat_file','in_file2')])])

220530-20:27:18,57 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.betweenMat, wf_laminar_fMRI_func_pRF.concatenateTransforms): No edge data
220530-20:27:18,57 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.betweenMat, wf_laminar_fMRI_func_pRF.concatenateTransforms): new edge data: {'connect': [('out', 'in_file')]}
220530-20:27:18,58 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.mcflirtWithinSess, wf_laminar_fMRI_func_pRF.concatenateTransforms): No edge data
220530-20:27:18,59 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.mcflirtWithinSess, wf_laminar_fMRI_func_pRF.concatenateTransforms): new edge data: {'connect': [('mat_file', 'in_file2')]}


In [45]:
#ConvertXFM.help()

Put all transformation matrices for given session in one folder

(Not the most elegant solution, but ApplyXfm4D requires a directory of tranformation mat files as input)

In [46]:
def copy_transforms(subject_id,sess_id,sess_nr,sess_nvol,mat_files,working_dir):
    from os.path import join as opj
    import shutil
    import os
    
    transformMatDir = opj(working_dir,'_subject_id_'+subject_id,
                         '_sess_id_'+sess_id+'_sess_nr_'+str(sess_nr)+'_sess_nvol_'+str(sess_nvol),
                         'transformMats')
    
    if not os.path.isdir(transformMatDir):
        os.mkdir(transformMatDir)
    
    for mat in mat_files:
        print('%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%')
        print(mat)
        print('%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%')

        # copy file
        shutil.copy(mat, transformMatDir)
        
        # remove .mat extension (this is how the ApplyXfm4D interface likes it)
        base=os.path.basename(mat)
        filename=os.path.splitext(base)[0]
        shutil.move(opj(transformMatDir,filename+'.mat'), opj(transformMatDir,filename)) 

    # session-dependent filename prefix
    prefix = f"MAT_000{sess_nr}_MAT_"

    return transformMatDir, prefix

In [47]:
copyTransforms = Node(Function(input_names = ['subject_id','sess_id','sess_nr', 'sess_nvol',
                                             'mat_files','working_dir'],
                               output_names=['transformMatDir','prefix'],
                               function=copy_transforms),
                      name='copyTransforms')
copyTransforms.inputs.working_dir = opj(der_dir,wf_name)

In [48]:
wf.connect([(subjects, copyTransforms, [('subject_id', 'subject_id')])])
wf.connect([(sessions, copyTransforms, [('sess_id', 'sess_id')])])
wf.connect([(sessions, copyTransforms, [('sess_nr', 'sess_nr')])])
wf.connect([(sessions, copyTransforms, [('sess_nvol', 'sess_nvol')])])
wf.connect([(concatenateTransforms, copyTransforms, [('out_file', 'mat_files')])])

220530-20:27:18,86 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.copyTransforms): No edge data
220530-20:27:18,87 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.subjects, wf_laminar_fMRI_func_pRF.copyTransforms): new edge data: {'connect': [('subject_id', 'subject_id')]}
220530-20:27:18,87 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.copyTransforms): No edge data
220530-20:27:18,88 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.copyTransforms): new edge data: {'connect': [('sess_id', 'sess_id')]}
220530-20:27:18,88 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.copyTransforms): Edge data exists: {'connect': [('sess_id', 'sess_id')]}
220530-20:27:18,88 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sessions, wf_laminar_fMRI_func_pRF.copyTransforms): new edge data: {'connect': [('sess_id', 'sess_id'), ('sess_nr', 'sess_nr')

Apply transformation matrices to realign within and between sessions in one step

In [49]:
applyRealign = Node(ApplyXfm4D(),name='applyRealign')

220530-20:27:18,95 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [50]:
wf.connect([(discardDummies,applyRealign,[('roi_file','in_file')])])
wf.connect([(discardDummies,applyRealign,[('roi_file','ref_vol')])])
wf.connect([(copyTransforms,applyRealign,[('transformMatDir','trans_dir')])])
wf.connect([(copyTransforms,applyRealign,[('prefix','user_prefix')])])

220530-20:27:18,101 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.discardDummies, wf_laminar_fMRI_func_pRF.applyRealign): No edge data
220530-20:27:18,101 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.discardDummies, wf_laminar_fMRI_func_pRF.applyRealign): new edge data: {'connect': [('roi_file', 'in_file')]}
220530-20:27:18,102 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.discardDummies, wf_laminar_fMRI_func_pRF.applyRealign): Edge data exists: {'connect': [('roi_file', 'in_file')]}
220530-20:27:18,102 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.discardDummies, wf_laminar_fMRI_func_pRF.applyRealign): new edge data: {'connect': [('roi_file', 'in_file'), ('roi_file', 'ref_vol')]}
220530-20:27:18,102 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.copyTransforms, wf_laminar_fMRI_func_pRF.applyRealign): No edge data
220530-20:27:18,103 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.copyTransforms, wf_laminar_fMRI_func_pRF.applyRealign): new edge data: {'conne

In [51]:
#ApplyXfm4D.help()

### Unwarping

fugue (FMRIB's Utility for Geometrically Unwarping EPIs) performs unwarping of an EPI image based on fieldmap data. The input required consists of the EPI image, the fieldmap (as an unwrapped phase map or a scaled fieldmap in rad/s) and appropriate image sequence parameters for the EPI and fieldmap acquisitions: the dwell time for EPI (also known as the echo spacing); and the echo time difference (called asym time herein). 

https://fsl.fmrib.ox.ac.uk/fsl/fslwiki/FUGUE/Guide

https://nipype.readthedocs.io/en/0.12.0/interfaces/generated/nipype.interfaces.fsl.preprocess.html#fugue

In [52]:
unwarping = Node(FUGUE(),name='unwarping')

# fugue -i epi --dwell=dwelltime --loadfmap=fieldmap -u result

220530-20:27:18,117 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [53]:
if unwarp:
    wf.connect([(applyRealign,unwarping,[('out_file','in_file')])])
    wf.connect([(acquisitionParams,unwarping,[('effective_echo_spacing','dwell_time')])])
    wf.connect([(prepFieldMap,unwarping,[('out_fieldmap','fmap_in_file')])])

### Slice-timing correction (SPM)

Parker & Razlighi, 2019: "The Benefit of Slice Timing Correction in Common fMRI Preprocessing Pipelines."
https://www.frontiersin.org/articles/10.3389/fnins.2019.00821/full

In [54]:
ref_slice = 1                           # (an integer (int or long))
                                        # 1-based Number of the reference slice

In [55]:
sliceTimingCorr = Node(SliceTiming(ref_slice=ref_slice),name='sliceTimingCorr')

220530-20:27:18,135 nipype.interface DEBUG:
	 matlab command or path has changed. recomputing version.
220530-20:27:18,138 nipype.interface DEBUG:
	 nodesktop_True
220530-20:27:18,139 nipype.interface DEBUG:
	 nosplash_True
220530-20:27:18,140 nipype.interface DEBUG:
	 single_comp_thread_True
220530-20:27:18,140 nipype.interface DEBUG:
	 nodesktop_True
220530-20:27:18,140 nipype.interface DEBUG:
	 nosplash_True
220530-20:27:18,141 nipype.interface DEBUG:
	 single_comp_thread_True
220530-20:27:28,965 nipype.interface DEBUG:
	 Command:
matlab -nodesktop -nosplash -nodesktop -nosplash -singleCompThread -r "fprintf(1,'Executing code at %s:\n',datestr(now));fprintf(1,'Executing code at %s:\n',datestr(now));ver,try,,if isempty(which('spm')),,throw(MException('SPMCheck:NotFound','SPM not in matlab path'));,end;,spm_path = spm('dir');,[name, version] = spm('ver');,fprintf(1, 'NIPYPE path:%s|name:%s|release:%s', spm_path, name, version);,exit;,        ,catch ME,fprintf(2,'MATLAB code threw an e

In [56]:
if unwarp:
    wf.connect([(unwarping,sliceTimingCorr,[('unwarped_file','in_files')])])
else:
    wf.connect([(applyRealign,sliceTimingCorr,[('out_file','in_files')])])
wf.connect([(acquisitionParams,sliceTimingCorr,[('num_slices','num_slices')])])
wf.connect([(acquisitionParams,sliceTimingCorr,[('slice_timing','slice_order')])])
wf.connect([(acquisitionParams,sliceTimingCorr,[('TR','time_repetition')])])
wf.connect([(acquisitionParams,sliceTimingCorr,[('TA','time_acquisition')])])

220530-20:27:28,998 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.applyRealign, wf_laminar_fMRI_func_pRF.sliceTimingCorr): No edge data
220530-20:27:28,998 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.applyRealign, wf_laminar_fMRI_func_pRF.sliceTimingCorr): new edge data: {'connect': [('out_file', 'in_files')]}
220530-20:27:28,999 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.acquisitionParams, wf_laminar_fMRI_func_pRF.sliceTimingCorr): No edge data
220530-20:27:28,999 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.acquisitionParams, wf_laminar_fMRI_func_pRF.sliceTimingCorr): new edge data: {'connect': [('num_slices', 'num_slices')]}
220530-20:27:29,0 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.acquisitionParams, wf_laminar_fMRI_func_pRF.sliceTimingCorr): Edge data exists: {'connect': [('num_slices', 'num_slices')]}
220530-20:27:29,0 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.acquisitionParams, wf_laminar_fMRI_func_pRF.sliceTimingCorr): new edge data:

In [57]:
#SliceTiming.help()

### Co-registration of functional and structural data (FreeSurfer bbregister, FLIRT FSL) 

Note: structural data is brought into functional space to avoid superfluous interpolation of functional volumes!

https://fsl.fmrib.ox.ac.uk/fsl/fslwiki/FLIRT

https://nipype.readthedocs.io/en/0.12.0/interfaces/generated/nipype.interfaces.fsl.preprocess.html#flirt



#### Concatenate functional runs

In [58]:
dimension = 't'
output_type = 'NIFTI'
merged_file = 'merged_func.nii'

In [59]:
concatenateFunc = JoinNode(Merge(dimension=dimension, output_type=output_type, merged_file=merged_file),
                        joinfield='in_files',
                        joinsource='sessions',
                        name="concatenateFunc")

220530-20:27:29,18 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
220530-20:27:29,19 nipype.workflow DEBUG:
	 Converted the join node concatenateFunc field in_files trait type from a legal value to a pathlike object or string representing an existing file


In [60]:
wf.connect([(sliceTimingCorr, concatenateFunc,[('timecorrected_files', 'in_files')])])

220530-20:27:29,24 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sliceTimingCorr, wf_laminar_fMRI_func_pRF.concatenateFunc): No edge data
220530-20:27:29,24 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.sliceTimingCorr, wf_laminar_fMRI_func_pRF.concatenateFunc): new edge data: {'connect': [('timecorrected_files', 'in_files')]}


#### Get mean functional volume

In [61]:
mean_vol = True                 # (a boolean) register to mean volume
save_mats = False               # (a boolean) save transformation parameters

In [62]:
meanFunc = Node(MCFLIRT(mean_vol = mean_vol, save_mats=save_mats), 
                    name='meanFunc')

220530-20:27:29,37 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [63]:
wf.connect([(concatenateFunc, meanFunc,[('merged_file', 'in_file')])])

220530-20:27:29,45 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.concatenateFunc, wf_laminar_fMRI_func_pRF.meanFunc): No edge data
220530-20:27:29,45 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.concatenateFunc, wf_laminar_fMRI_func_pRF.meanFunc): new edge data: {'connect': [('merged_file', 'in_file')]}


In [64]:
MCFLIRT.help()

Wraps the executable command ``mcflirt``.

FSL MCFLIRT wrapper for within-modality motion correction

For complete details, see the `MCFLIRT Documentation.
<https://fsl.fmrib.ox.ac.uk/fsl/fslwiki/MCFLIRT>`_

Examples
--------
>>> from nipype.interfaces import fsl
>>> mcflt = fsl.MCFLIRT()
>>> mcflt.inputs.in_file = 'functional.nii'
>>> mcflt.inputs.cost = 'mutualinfo'
>>> mcflt.inputs.out_file = 'moco.nii'
>>> mcflt.cmdline
'mcflirt -in functional.nii -cost mutualinfo -out moco.nii'
>>> res = mcflt.run()  # doctest: +SKIP

Inputs::

        [Mandatory]
        in_file: (a pathlike object or string representing an existing file)
                timeseries to motion-correct
                argument: ``-in %s``, position: 0

        [Optional]
        out_file: (a pathlike object or string representing a file)
                file to write
                argument: ``-out %s``
        cost: ('mutualinfo' or 'woods' or 'corratio' or 'normcorr' or
                  'normmi' or 'leastsquares

#### Make functional brain mask for coregistration

In [65]:
thresh = 800

dilate = 2 # voxels

In [66]:
binarizeMeanFunc = Node(Binarize(min=thresh, dilate=dilate),name='binarizeMeanFunc')


In [67]:
wf.connect([(meanFunc,binarizeMeanFunc,[('mean_img','in_file')])])

220530-20:27:29,75 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.meanFunc, wf_laminar_fMRI_func_pRF.binarizeMeanFunc): No edge data
220530-20:27:29,75 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.meanFunc, wf_laminar_fMRI_func_pRF.binarizeMeanFunc): new edge data: {'connect': [('mean_img', 'in_file')]}


#### Coregister structural image to mean functional (FLIRT)

In [68]:
out_matrix_file = 'struct2func.mat'     # (a pathlike object or string representing a file)
                                        # output affine matrix in 4x4 asciii format
apply_xfm = True                        # (a boolean)
                                        # apply transformation supplied by in_matrix_file or uses_qform to use
                                        # the affine matrix stored in the reference header
coarse_search = 4
fine_search = 2

In [69]:
if coreg_method == 'flirt':
    coreg = Node(FLIRT(),name='coreg')
    
    # out_matrix_file=out_matrix_file, coarse_search=coarse_search, fine_search=fine_search

In [70]:
if coreg_method == 'flirt':
    wf.connect([(convertT1ToNii, coreg,[('out_file', 'in_file')])])        
    #wf.connect([(convertT1ToNii, coreg,[('out_file', 'reference')])])   
    wf.connect([(meanFunc, coreg,[('mean_img', 'reference')])])  
    
    if manual_edits:
        wf.connect([(datasourceManualEdits, coreg,[('coreg_itksnap_struct2func_txt', 'in_matrix_file')])])
        coreg.inputs.apply_xfm = apply_xfm

In [71]:
FLIRT.help()

Wraps the executable command ``flirt``.

FSL FLIRT wrapper for coregistration

For complete details, see the `FLIRT Documentation.
<https://fsl.fmrib.ox.ac.uk/fsl/fslwiki/FLIRT>`_

To print out the command line help, use:
    fsl.FLIRT().inputs_help()

Examples
--------
>>> from nipype.interfaces import fsl
>>> from nipype.testing import example_data
>>> flt = fsl.FLIRT(bins=640, cost_func='mutualinfo')
>>> flt.inputs.in_file = 'structural.nii'
>>> flt.inputs.reference = 'mni.nii'
>>> flt.inputs.output_type = "NIFTI_GZ"
>>> flt.cmdline # doctest: +ELLIPSIS
'flirt -in structural.nii -ref mni.nii -out structural_flirt.nii.gz -omat structural_flirt.mat -bins 640 -searchcost mutualinfo'
>>> res = flt.run() #doctest: +SKIP

Inputs::

        [Mandatory]
        in_file: (a pathlike object or string representing an existing file)
                input file
                argument: ``-in %s``, position: 0
        reference: (a pathlike object or string representing an existing
              

#### Coregister structural image to mean functional (FS)

not done!

In [72]:
# contrast_type = 't2'


In [73]:
# if coreg_method == 'freesurfer':
#     #coreg = Node(MRICoreg(),name='coreg')
    
#     coreg = Node(BBRegister(contrast_type=contrast_type),name='coreg')

In [74]:
# if coreg_method == 'freesurfer':
#     wf.connect([(convertT1ToNii, coreg,[('out_file', 'source_file')])])
#     if manual_edits:
#         wf.connect([(datasourceManualEdits, coreg,[('coreg_itksnap_txt','init_reg_file')])])
            
#     wf.connect([(meanFunc, coreg,[('mean_img', 'source_file')])])

In [75]:
# BBRegister.help()

#### Coregister structural image to mean functional (apply manual ITK-snap correction)
https://layerfmri.com/2019/02/11/high-quality-registration/


##### Mandatory inputs
input_image (a pathlike object or string representing an existing file) – Image to apply transformation to (generally a coregistered functional). Maps to a command-line argument: --input %s.

reference_image (a pathlike object or string representing an existing file) – Reference image space that you wish to warp INTO. Maps to a command-line argument: --reference-image %s.

transforms (a list of items which are a pathlike object or string representing an existing file or ‘identity’) – Transform files: will be applied in reverse order. For example, the last specified transform will be applied first. Maps to a command-line argument: %s.

##### Optional inputs
args (a string) – Additional parameters to the command. Maps to a command-line argument: %s.

default_value (a float) – Maps to a command-line argument: --default-value %g. (Nipype default value: 0.0)

dimension (2 or 3 or 4) – This option forces the image to be treated as a specified-dimensional image. If not specified, antsWarp tries to infer the dimensionality from the input image. Maps to a command-line argument: --dimensionality %d.

environ (a dictionary with keys which are a bytes or None or a value of class ‘str’ and with values which are a bytes or None or a value of class ‘str’) – Environment variables. (Nipype default value: {})

float (a boolean) – Use float instead of double for computations. Maps to a command-line argument: --float %d. (Nipype default value: False)

input_image_type (0 or 1 or 2 or 3) – Option specifying the input image type of scalar (default), vector, tensor, or time series. Maps to a command-line argument: --input-image-type %d.

interpolation (‘Linear’ or ‘NearestNeighbor’ or ‘CosineWindowedSinc’ or ‘WelchWindowedSinc’ or ‘HammingWindowedSinc’ or ‘LanczosWindowedSinc’ or ‘MultiLabel’ or ‘Gaussian’ or ‘BSpline’) – Maps to a command-line argument: %s. (Nipype default value: Linear)

interpolation_parameters (a tuple of the form: (an integer) or a tuple of the form: (a float, a float))

invert_transform_flags (a list of items which are a boolean)

num_threads (an integer) – Number of ITK threads to use. (Nipype default value: 1)

out_postfix (a string) – Postfix that is appended to all output files (default = _trans). (Nipype default value: _trans)

output_image (a string) – Output file name. Maps to a command-line argument: --output %s.

print_out_composite_warp_file (a boolean) – Output a composite warp file instead of a transformed image. Requires inputs: output_image.



In [76]:
#antsApplyTransforms --interpolation BSpline[5] -d 3 -i MP2RAGE.nii -r EPI.nii -t initial_matrix.txt -o registered_applied.nii

In [77]:
interpolation = 'BSpline'
dimension = 3


In [78]:
if coreg_method == 'itk-snap':
    coreg = Node(ApplyTransforms(interpolation=interpolation,
                                dimension=dimension), name='coreg')

In [79]:
if coreg_method == 'itk-snap':
    wf.connect([(convertT1ToNii, coreg,[('out_file', 'input_image')])])        
    wf.connect([(meanFunc, coreg,[('mean_img', 'reference_image')])])  
    wf.connect([(datasourceManualEdits, coreg,[('coreg_itksnap_struct2func_txt', 'transforms')])])

#### Coregister structural image to mean functional (ANTs)
https://layerfmri.com/2019/02/11/high-quality-registration/

antsRegistration \
--verbose 1 \
--dimensionality 3 \
--float 1 \
--output [registered_,registered_Warped.nii.gz,registered_InverseWarped.nii.gz] \
--interpolation Linear \
--use-histogram-matching 0 \
--winsorize-image-intensities [0.005,0.995] \
--initial-moving-transform initial_matrix.txt \
--transform Rigid[0.05] \
--metric CC[static_image.nii,moving_image.nii,0.7,32,Regular,0.1] \
--convergence [1000x500,1e-6,10] \
--shrink-factors 2x1 \
--smoothing-sigmas 1x0vox \
--transform Affine[0.1] \
--metric MI[static_image.nii,moving_image.nii,0.7,32,Regular,0.1] \
--convergence [1000x500,1e-6,10] \
--shrink-factors 2x1 \
--smoothing-sigmas 1x0vox \
--transform SyN[0.1,2,0] \
--metric CC[static_image.nii,moving_image.nii,1,2] \
--convergence [500x100,1e-6,10] \
--shrink-factors 2x1 \
--smoothing-sigmas 1x0vox \
-x mask.nii


See also: https://github.com/ANTsX/ANTs/wiki/Anatomy-of-an-antsRegistration-call

about masking: https://github.com/ANTsX/ANTs/issues/483

In [80]:
verbose = True                          # (a boolean, nipype default value: False)
                                        # argument: ``-v``
    
dimension = 3                           # dimension: (3 or 2, nipype default value: 3)
                                        # image dimension (2 or 3)
                                        # argument: ``--dimensionality %d``
        
float = True                            # (a boolean)
                                        # Use float instead of double for computations.
                                        # argument: ``--float %d``
        
output_transform_prefix = 'registered_' # (a string, nipype default value: transform)
                                        # argument: ``%s``
    
output_warped_image = 'registered_Warped.nii.gz'              
                                        # (a boolean or a pathlike object or string
                                        # representing a file)
    
output_inverse_warped_image = 'registered_InverseWarped.nii.gz'       
                                        # (a boolean or a pathlike object or
                                        # string representing a file)
                                        # requires: output_warped_image
        
interpolation = 'Linear'                # ('Linear' or 'NearestNeighbor' or 'CosineWindowedSinc'
                                        # or 'WelchWindowedSinc' or 'HammingWindowedSinc' or
                                        # 'LanczosWindowedSinc' or 'BSpline' or 'MultiLabel' or 'Gaussian',
                                        # nipype default value: Linear)
                                        # argument: ``%s``   
                
use_histogram_matching = False          #  (a boolean or a list of items which are a
                                        # boolean, nipype default value: True)
                                        # Histogram match the images before registration. 
        
winsorize_lower_quantile = 0.001        # (0.0 <= a floating point number <= 1.0,
                                        # nipype default value: 0.0)
                                        # The Lower quantile to clip image ranges
                                        # argument: ``%s``
            
winsorize_upper_quantile = 0.999        # (0.0 <= a floating point number <= 1.0,
                                        # nipype default value: 1.0)
                                        # The Upper quantile to clip image ranges
                                        # argument: ``%s``
            
#initial_moving_transform = 'initial_matrix.txt'   # (a list of items which are an existing file
                                        # name)
                                        # A transform or a list of transforms that should be appliedbefore the
                                        # registration begins. Note that, when a list is given,the
                                        # transformations are applied in reverse order.
                                        # argument: ``%s``
                                        # mutually_exclusive: initial_moving_transform_com
                        
transforms = ['Rigid','SyN']   # (a list of items which are 'Rigid' or 'Affine' or
                                        # 'CompositeAffine' or 'Similarity' or 'Translation' or 'BSpline' or
                                        # 'GaussianDisplacementField' or 'TimeVaryingVelocityField' or
                                        # 'TimeVaryingBSplineVelocityField' or 'SyN' or 'BSplineSyN' or
                                        # 'Exponential' or 'BSplineExponential')
                                        # argument: ``%s``
                    
transform_parameters = [(0.1,),(0.2,4.0,3.0)]        
                                        # (a list of items which are a tuple of the form:
                                        # (a float) or a tuple of the form: (a float, a float, a float) or a
                                        # tuple of the form: (a float, an integer (int or long), an integer
                                        # (int or long), an integer (int or long)) or a tuple of the form:
                                        # (a float, an integer (int or long), a float, a float, a float, a
                                        # float) or a tuple of the form: (a float, a float, a float, an
                                        # integer (int or long)) or a tuple of the form: (a float, an
                                        # integer (int or long), an integer (int or long), an integer (int
                                        # or long), an integer (int or long)))
                                
metric = ['CC', 'CC']                   # (a list of items which are 'CC' or 'MeanSquares' or 'Demons'
                                        # or 'GC' or 'MI' or 'Mattes' or a list of items which are 'CC' or
                                        # 'MeanSquares' or 'Demons' or 'GC' or 'MI' or 'Mattes')
                                        # the metric(s) to use for each stage. Note that multiple metrics per
                                        # stage are not supported in ANTS 1.9.1 and earlier.
                
metric_weight = [1,1]             # (a list of items which are a float or a list of items
                                        # which are a float, nipype default value: [1.0])
                                        # the metric weight(s) for each stage. The weights must sum to 1 per
                                        # stage.
                                        # requires: metric
                
radius_or_number_of_bins = [5,5]    # (a list of items which are an integer (int
                                        # or long) or a list of items which are an integer (int or long),
                                        # nipype default value: [5])
                                        # the number of bins in each stage for the MI and Mattes metric, the
                                        # radius for other metrics
                                        # requires: metric_weight
                    
sampling_strategy = ['Random','Random']              
                                        # (a list of items which are 'None' or 'Regular' or
                                        # 'Random' or None or a list of items which are 'None' or 'Regular'
                                        # or 'Random' or None)
                                        # the metric sampling strategy (strategies) for each stage
                                        # requires: metric_weight
                
sampling_percentage = [0.3,0.3]     # (a list of items which are 0.0 <= a floating
                                        # point number <= 1.0 or None or a list of items which are 0.0 <= a
                                        # floating point number <= 1.0 or None)
                                        # the metric sampling percentage(s) to use for each stage
                                        # requires: sampling_strategy
                
convergence_threshold = [1e-6,1e-6]# (a list of at least 1 items which are a float,
                                        # nipype default value: [1e-06])
                                        # requires: number_of_iterations
        
convergence_window_size = [10,5]    # (a list of at least 1 items which are an
                                        # integer (int or long), nipype default value: [10])
                                        # requires: convergence_threshold
        
number_of_iterations = [[1000,1000,1000,1000],[50,50,150,100]]       
                                        # (a list of items which are a list of items
                                        # which are an integer (int or long))                
                                        
shrink_factors = [[1,1,1,1], [3,2,2,1]]  # (a list of items which are a list of items which are
                                        # an integer (int or long))
    
smoothing_sigmas = [[4.0,3.0,2.0,1.0], [2.0,1.0,0.5,0.0]]# (a list of items which are a list of items which
                                        # are a float)


<!-- verbose = True                          # (a boolean, nipype default value: False)
                                        # argument: ``-v``
    
dimension = 3                           # dimension: (3 or 2, nipype default value: 3)
                                        # image dimension (2 or 3)
                                        # argument: ``--dimensionality %d``
        
float = True                            # (a boolean)
                                        # Use float instead of double for computations.
                                        # argument: ``--float %d``
        
output_transform_prefix = 'registered_' # (a string, nipype default value: transform)
                                        # argument: ``%s``
    
output_warped_image = 'registered_Warped.nii.gz'              
                                        # (a boolean or a pathlike object or string
                                        # representing a file)
    
output_inverse_warped_image = 'registered_InverseWarped.nii.gz'       
                                        # (a boolean or a pathlike object or
                                        # string representing a file)
                                        # requires: output_warped_image
        
interpolation = 'Linear'                # ('Linear' or 'NearestNeighbor' or 'CosineWindowedSinc'
                                        # or 'WelchWindowedSinc' or 'HammingWindowedSinc' or
                                        # 'LanczosWindowedSinc' or 'BSpline' or 'MultiLabel' or 'Gaussian',
                                        # nipype default value: Linear)
                                        # argument: ``%s``   
                
use_histogram_matching = False          #  (a boolean or a list of items which are a
                                        # boolean, nipype default value: True)
                                        # Histogram match the images before registration. 
        
winsorize_lower_quantile = 0.001        # (0.0 <= a floating point number <= 1.0,
                                        # nipype default value: 0.0)
                                        # The Lower quantile to clip image ranges
                                        # argument: ``%s``
            
winsorize_upper_quantile = 0.999        # (0.0 <= a floating point number <= 1.0,
                                        # nipype default value: 1.0)
                                        # The Upper quantile to clip image ranges
                                        # argument: ``%s``
            
#initial_moving_transform = 'initial_matrix.txt'   # (a list of items which are an existing file
                                        # name)
                                        # A transform or a list of transforms that should be appliedbefore the
                                        # registration begins. Note that, when a list is given,the
                                        # transformations are applied in reverse order.
                                        # argument: ``%s``
                                        # mutually_exclusive: initial_moving_transform_com
                        
transforms = ['Rigid','Affine','SyN']   # (a list of items which are 'Rigid' or 'Affine' or
                                        # 'CompositeAffine' or 'Similarity' or 'Translation' or 'BSpline' or
                                        # 'GaussianDisplacementField' or 'TimeVaryingVelocityField' or
                                        # 'TimeVaryingBSplineVelocityField' or 'SyN' or 'BSplineSyN' or
                                        # 'Exponential' or 'BSplineExponential')
                                        # argument: ``%s``
                    
transform_parameters = [(0.1,), (0.1,), (0.2,4.0,3.0)]        
                                        # (a list of items which are a tuple of the form:
                                        # (a float) or a tuple of the form: (a float, a float, a float) or a
                                        # tuple of the form: (a float, an integer (int or long), an integer
                                        # (int or long), an integer (int or long)) or a tuple of the form:
                                        # (a float, an integer (int or long), a float, a float, a float, a
                                        # float) or a tuple of the form: (a float, a float, a float, an
                                        # integer (int or long)) or a tuple of the form: (a float, an
                                        # integer (int or long), an integer (int or long), an integer (int
                                        # or long), an integer (int or long)))
                                
metric = ['CC','MI','CC']               # (a list of items which are 'CC' or 'MeanSquares' or 'Demons'
                                        # or 'GC' or 'MI' or 'Mattes' or a list of items which are 'CC' or
                                        # 'MeanSquares' or 'Demons' or 'GC' or 'MI' or 'Mattes')
                                        # the metric(s) to use for each stage. Note that multiple metrics per
                                        # stage are not supported in ANTS 1.9.1 and earlier.
                
metric_weight = [1,1,1]             # (a list of items which are a float or a list of items
                                        # which are a float, nipype default value: [1.0])
                                        # the metric weight(s) for each stage. The weights must sum to 1 per
                                        # stage.
                                        # requires: metric
                
radius_or_number_of_bins = [5,5,5]    # (a list of items which are an integer (int
                                        # or long) or a list of items which are an integer (int or long),
                                        # nipype default value: [5])
                                        # the number of bins in each stage for the MI and Mattes metric, the
                                        # radius for other metrics
                                        # requires: metric_weight
                    
sampling_strategy = ['Random','Random','Random']              
                                        # (a list of items which are 'None' or 'Regular' or
                                        # 'Random' or None or a list of items which are 'None' or 'Regular'
                                        # or 'Random' or None)
                                        # the metric sampling strategy (strategies) for each stage
                                        # requires: metric_weight
                
sampling_percentage = [0.3,0.3,0.3]     # (a list of items which are 0.0 <= a floating
                                        # point number <= 1.0 or None or a list of items which are 0.0 <= a
                                        # floating point number <= 1.0 or None)
                                        # the metric sampling percentage(s) to use for each stage
                                        # requires: sampling_strategy
                
convergence_threshold = [1e-6,1e-6,1e-6]# (a list of at least 1 items which are a float,
                                        # nipype default value: [1e-06])
                                        # requires: number_of_iterations
        
convergence_window_size = [10,10,5]    # (a list of at least 1 items which are an
                                        # integer (int or long), nipype default value: [10])
                                        # requires: convergence_threshold
        
number_of_iterations = [[1000,1000,1000,1000],[1000,1000,1000,1000],[50,50,150,100]]       
                                        # (a list of items which are a list of items
                                        # which are an integer (int or long))                
                                        
shrink_factors = [[1,1,1,1], [1,1,1,1], [3,2,2,1]]  # (a list of items which are a list of items which are
                                        # an integer (int or long))
    
smoothing_sigmas = [[4.0,3.0,2.0,1.0], [4.0,3.0,2.0,1.0], [2.0,1.0,0.5,0.0]]# (a list of items which are a list of items which
                                        # are a float)
 -->

In [81]:
# check = Registration(verbose=verbose,
#           dimension=dimension,
#           float=float,
#           output_transform_prefix=output_transform_prefix,
#           output_warped_image=output_warped_image,
#           output_inverse_warped_image=output_inverse_warped_image,
#           interpolation=interpolation, 
#           use_histogram_matching=use_histogram_matching,
#           winsorize_lower_quantile=winsorize_lower_quantile,
#           winsorize_upper_quantile=winsorize_upper_quantile, 
#           transforms=transforms, 
#           transform_parameters=transform_parameters,
#           metric=metric, 
#           metric_weight=metric_weight, 
#           radius_or_number_of_bins=radius_or_number_of_bins,
#           sampling_strategy=sampling_strategy, 
#           sampling_percentage=sampling_percentage,
#           convergence_threshold=convergence_threshold, 
#           convergence_window_size=convergence_window_size,
#           number_of_iterations=number_of_iterations, 
#           shrink_factors=shrink_factors, 
#           smoothing_sigmas=smoothing_sigmas,
#           fixed_image='/scratch/mayaaj90/7T-ret/test/fixed_image.nii',
#           moving_image='/scratch/mayaaj90/7T-ret/test/moving_image.nii',
#           initial_moving_transform='/scratch/mayaaj90/7T-ret/test/coreg_itksnap_struct2func.txt')
# check.cmdline

<!-- antsRegistration 
-v 
--dimensionality 3
--float 1 
--output [ registered_, registered_Warped.nii.gz, registered_InverseWarped.nii.gz ] 
--interpolation Linear 
--use-histogram-matching 0 
--winsorize-image-intensities [ 0.005, 0.995 ]  
--initial-moving-transform [ /scratch/mayaaj90/7T-ret/test/coreg_itksnap_struct2func.txt, 0 ] 
--transform Rigid[ 0.05 ] 
--metric CC[ /scratch/mayaaj90/7T-ret/test/fixed_image.nii, /scratch/mayaaj90/7T-ret/test/moving_image.nii, 0.7, 32, Regular, 0.1 ] 
--convergence [ 1000x500, 1e-06, 10 ] 
--smoothing-sigmas 1.0x0.0 
--shrink-factors 2x1 
--use-histogram-matching 0 
--transform Affine[ 0.1 ] 
--metric MI[ /scratch/mayaaj90/7T-ret/test/fixed_image.nii, /scratch/mayaaj90/7T-ret/test/moving_image.nii, 0.7, 32, Regular, 0.1 ] 
--convergence [ 1000x500, 1e-06, 10 ] 
--smoothing-sigmas 1.0x0.0 
--shrink-factors 2x1 
--use-histogram-matching 0 
--transform SyN[ 0.1, 2.0, 0.0 ] 
--metric CC[ /scratch/mayaaj90/7T-ret/test/fixed_image.nii, /scratch/mayaaj90/7T-ret/test/moving_image.nii, 1, 2 ] 
--convergence [ 500x100, 1e-06, 10 ] 
--smoothing-sigmas 1.0x0.0 
--shrink-factors 2x1 
--write-composite-transform 0
--collapse-output-transforms 1 
--initialize-transforms-per-stage 0  -->

In [82]:
# antsRegistration 
# --collapse-output-transforms 0 
# --dimensionality 3 
# --float 1 
# --initial-moving-transform [ /scratch/mayaaj90/7T-ret/manualcorr/sub-01/coreg_itksnap_struct2func.txt, 0 ] 
# --initialize-transforms-per-stage 0 
# --interpolation Linear 
# --output [ output_, output_warped_image.nii.gz ] 
# --transform Rigid[ 0.1 ] 
# --metric CC[ /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/meanFunc/merged_func_mcf.nii_mean_reg.nii, /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/convertT1ToNii/T1_out.nii, 1, 5, Random, 0.3 ] 
# --convergence [ 1000x1000x1000x1000, 1e-06, 10 ] 
# --smoothing-sigmas 4.0x3.0x2.0x1.0vox 
# --shrink-factors 1x1x1x1 
# --use-histogram-matching 0 
# --transform SyN[ 0.2, 4.0, 3.0 ] 
# --metric CC[ /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/meanFunc/merged_func_mcf.nii_mean_reg.nii, /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/convertT1ToNii/T1_out.nii, 1, 5, Random, 0.3 ] 
# --convergence [ 50x50x150x100, 1e-06, 5 ] 
# --smoothing-sigmas 2.0x1.0x0.5x0.0vox 
# --shrink-factors 3x2x2x1 
# --use-histogram-matching 0 
# --winsorize-image-intensities [ 0.001, 0.999 ]  
# --write-composite-transform 0


In [83]:
# antsRegistration 
# --collapse-output-transforms 1 
# --dimensionality 3 
# --masks [ /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/binarizeMeanFunc/merged_func_mcf.nii_mean_reg_thresh.nii, /scratch/mayaaj90/7T-ret/output/freesurfer_externalbrainmask/_subject_id_sub-01/brainmask.nii ] --float 1 --initial-moving-transform [ /scratch/mayaaj90/7T-ret/manualcorr/sub-01/coreg_itksnap_struct2func.txt, 0 ] --initialize-transforms-per-stage 0 --interpolation Linear --output [ registered_, registered_Warped.nii.gz, registered_InverseWarped.nii.gz ] --transform Rigid[ 0.1 ] --metric CC[ /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/meanFunc/merged_func_mcf.nii_mean_reg.nii, /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/convertT1ToNii/T1_out.nii, 1, 5, Random, 0.3 ] --convergence [ 1000x1000x1000x1000, 1e-06, 10 ] --smoothing-sigmas 4.0x3.0x2.0x1.0 --shrink-factors 1x1x1x1 --use-histogram-matching 0 --transform SyN[ 0.2, 4.0, 3.0 ] --metric CC[ /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/meanFunc/merged_func_mcf.nii_mean_reg.nii, /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/convertT1ToNii/T1_out.nii, 1, 5, Random, 0.3 ] --convergence [ 50x50x150x100, 1e-06, 5 ] --smoothing-sigmas 2.0x1.0x0.5x0.0 --shrink-factors 3x2x2x1 --use-histogram-matching 0 -v --winsorize-image-intensities [ 0.001, 0.999 ]  --write-composite-transform 0


In [84]:
# works:
# reg = Registration()
# reg.inputs.fixed_image = '/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/meanFunc/merged_func_mcf.nii_mean_reg.nii'
# reg.inputs.moving_image = '/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/convertT1ToNii/T1_out.nii'
# reg.inputs.output_transform_prefix = "output_"
# reg.inputs.output_warped_image = 'output_Warped.nii.gz'
# reg.inputs.output_inverse_warped_image = 'output_InverseWarped.nii.gz'
# reg.inputs.interpolation = 'Linear'
# reg.inputs.initial_moving_transform = '/scratch/mayaaj90/7T-ret/manualcorr/sub-01/coreg_itksnap_struct2func.txt'
# reg.inputs.dimension = 3
# reg.inputs.write_composite_transform = False
# reg.inputs.collapse_output_transforms = False
# reg.inputs.initialize_transforms_per_stage = False
# reg.inputs.float = True
# reg.inputs.transforms = ['Rigid', 'SyN']
# reg.inputs.transform_parameters = [(0.1,), (0.2, 4.0, 3.0)]
# reg.inputs.use_histogram_matching = [False, False] # This is the default
# reg.inputs.verbose = True
# reg.inputs.number_of_iterations = [[1000,1000,1000,1000], [50,50,150,100]]

# reg.inputs.metric = ['CC']*2
# reg.inputs.metric_weight = [1]*2 # Default (value ignored currently by ANTs)
# reg.inputs.radius_or_number_of_bins = [5]*2
# reg.inputs.sampling_strategy = ['Random', 'Random']
# reg.inputs.sampling_percentage = [0.3, 0.3]

# reg.inputs.convergence_threshold = [1.e-6, 1.e-6]
# reg.inputs.convergence_window_size = [10,5]
# reg.inputs.smoothing_sigmas = [[4.0,3.0,2.0,1.0], [2.0,1.0,0.5,0.0]]
# reg.inputs.sigma_units = ['vox'] * 2
# reg.inputs.shrink_factors = [[1,1,1,1], [3,2,2,1]]

# reg.inputs.winsorize_lower_quantile = 0.001
# reg.inputs.winsorize_upper_quantile = 0.999

# reg.inputs.fixed_image_masks = ['/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/binarizeMeanFunc/merged_func_mcf.nii_mean_reg_thresh.nii', '/scratch/mayaaj90/7T-ret/output/freesurfer_externalbrainmask/_subject_id_sub-01/brainmask.nii']
# reg.cmdline
# reg.run()  

<!-- class AntsRegistrationInputSpec(CommandLineInputSpec):
    fixed_image = File(desc="File", exists=True, mandatory=True, argstr="%s")
    
    
    moving_image = File(desc="File", exists=True, mandatory=True, argstr="%s")
    fixed_image_mask = File(desc="File", exists=True, mandatory=True, argstr="%s")
    moving_image_mask = File(desc="File", exists=True, mandatory=True, argstr="%s")
    initial_moving_transform = File(desc="File", exists=True, mandatory=True, argstr="%s")
    
    filename_uni = File(exists=True, mandatory=True, desc='the input UNI image')
    filename_inv1 = File(exists=True, mandatory=True, desc='the input INV1 image')
    filename_inv2 = File(exists=True, mandatory=True, desc='the input INV2 image')
    filename_output = File(mandatory=True, desc='the output denoised image') # Do not set exists=True !!
    multiplying_factor = traits.Int(7, desc='the multiplying factor')
        
class AntsRegistrationOutputSpec(TraitedSpec):
    filename_output = File(desc='the output denoised image')

class AntsRegistration(CommandLine):
    input_spec = AntsRegistrationInputSpec
    output_spec = AntsRegistrationOutputSpec
    
    def _run_interface(self, runtime):

        # Call our python code here:
        mp2rage_robust_combination(
            self.inputs.filename_uni,
            self.inputs.filename_inv1,
            self.inputs.filename_inv2,
            self.inputs.filename_output,
            self.inputs.multiplying_factor
        )
        # And we are done
        return runtime

    def _list_outputs(self):
        return {'filename_output': self.inputs.filename_output} -->

In [85]:
if coreg_method == 'antsRegistration':
    coreg = Node(Registration(verbose=verbose,
                              dimension=dimension,
                              float=float,
                              output_transform_prefix=output_transform_prefix,
                              output_warped_image=output_warped_image,
                              output_inverse_warped_image=output_inverse_warped_image,
                              interpolation=interpolation, 
                              use_histogram_matching=use_histogram_matching,
                              winsorize_lower_quantile=winsorize_lower_quantile,
                              winsorize_upper_quantile=winsorize_upper_quantile, 
                              transforms=transforms, 
                              transform_parameters=transform_parameters,
                              metric=metric, 
                              metric_weight=metric_weight, 
                              radius_or_number_of_bins=radius_or_number_of_bins,
                              sampling_strategy=sampling_strategy, 
                              sampling_percentage=sampling_percentage,
                              convergence_threshold=convergence_threshold, 
                              convergence_window_size=convergence_window_size,
                              number_of_iterations=number_of_iterations, 
                              shrink_factors=shrink_factors, 
                              smoothing_sigmas=smoothing_sigmas),
                 name='coreg')
    

In [86]:
if coreg_method == 'antsRegistration':
    if coreg_dir == 'func2struct':
        # when moving func 2 struct
        wf.connect([(convertT1ToNii, coreg,[('out_file', 'fixed_image')])])    
        wf.connect([(meanFunc, coreg,[('mean_img', 'moving_image')])])
        wf.connect([(datasourceManualEdits, coreg,[('coreg_itksnap_func2struct_txt', 'initial_moving_transform')])])    
        wf.connect([(datasource, coreg,[('brainmask', 'fixed_image_masks')])])
        wf.connect([(binarizeMeanFunc, coreg,[('binary_file', 'moving_image_masks')])])
    
    elif coreg_dir == 'struct2func':
        # when moving struct 2 func:
        wf.connect([(meanFunc, coreg,[('mean_img', 'fixed_image')])]) 
        wf.connect([(convertT1ToNii, coreg,[('out_file', 'moving_image')])])
        wf.connect([(datasourceManualEdits, coreg,[('coreg_itksnap_struct2func_txt', 'initial_moving_transform')])])
        wf.connect([(datasource, coreg,[('brainmask', 'moving_image_masks')])])
        wf.connect([(binarizeMeanFunc, coreg,[('binary_file', 'fixed_image_masks')])])
        #wf.connect([(datasourceManualEdits, coreg,[('coreg_itksnap_T1', 'moving_image')])]) 

# fixed_image: (a list of items which are an existing file name)
#         Image to which the moving_image should be transformed(usually a
#         structural image)
# moving_image: (a list of items which are an existing file name)
#         Image that will be registered to the space of fixed_image. This is
#         theimage on which the transformations will be applied to

220530-20:27:34,441 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.meanFunc, wf_laminar_fMRI_func_pRF.coreg): No edge data
220530-20:27:34,442 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.meanFunc, wf_laminar_fMRI_func_pRF.coreg): new edge data: {'connect': [('mean_img', 'fixed_image')]}
220530-20:27:34,442 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.convertT1ToNii, wf_laminar_fMRI_func_pRF.coreg): No edge data
220530-20:27:34,442 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.convertT1ToNii, wf_laminar_fMRI_func_pRF.coreg): new edge data: {'connect': [('out_file', 'moving_image')]}
220530-20:27:34,443 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasourceManualEdits, wf_laminar_fMRI_func_pRF.coreg): No edge data
220530-20:27:34,443 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasourceManualEdits, wf_laminar_fMRI_func_pRF.coreg): new edge data: {'connect': [('coreg_itksnap_struct2func_txt', 'initial_moving_transform')]}
220530-20:27:34,443 nipype.wor

In [87]:
Registration.help()

Wraps the executable command ``antsRegistration``.

ANTs Registration command for registration of images

`antsRegistration <http://stnava.github.io/ANTs/>`_ registers a ``moving_image`` to a ``fixed_image``,
using a predefined (sequence of) cost function(s) and transformation operations.
The cost function is defined using one or more 'metrics', specifically
local cross-correlation (``CC``), Mean Squares (``MeanSquares``), Demons (``Demons``),
global correlation (``GC``), or Mutual Information (``Mattes`` or ``MI``).

ANTS can use both linear (``Translation``, ``Rigid``, ``Affine``, ``CompositeAffine``,
or ``Translation``) and non-linear transformations (``BSpline``, ``GaussianDisplacementField``,
``TimeVaryingVelocityField``, ``TimeVaryingBSplineVelocityField``, ``SyN``, ``BSplineSyN``,
``Exponential``, or ``BSplineExponential``). Usually, registration is done in multiple
*stages*. For example first an Affine, then a Rigid, and ultimately a non-linear
(Syn)-transformation.

antsRegist

#### Prepare mask for pRF mapping

Apply registration transformation to gray matter mask

antsApplyTransforms --interpolation BSpline[5] -d 3 -i moving_image.nii -r reference_image.nii -t registered_1Warp.nii.gz -t registered_0GenericAffine.mat -o registered_applied.nii

In [88]:
#ApplyTransforms.help()
#output_image

In [89]:
interpolation = 'NearestNeighbor'

In [90]:
coregGM = Node(ApplyTransforms(interpolation=interpolation), name='coregGM')

In [91]:
if coreg_method == 'antsRegistration':
    if coreg_dir == 'struct2func':
        wf.connect([(coreg, coregGM,[('forward_transforms', 'transforms')])]) 
        wf.connect([(datasource, coregGM,[('GM', 'input_image')])])
        wf.connect([(meanFunc, coregGM,[('mean_img', 'reference_image')])])


220530-20:27:34,481 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.coreg, wf_laminar_fMRI_func_pRF.coregGM): No edge data
220530-20:27:34,482 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.coreg, wf_laminar_fMRI_func_pRF.coregGM): new edge data: {'connect': [('forward_transforms', 'transforms')]}
220530-20:27:34,482 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.coregGM): No edge data
220530-20:27:34,483 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasource, wf_laminar_fMRI_func_pRF.coregGM): new edge data: {'connect': [('GM', 'input_image')]}
220530-20:27:34,483 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.meanFunc, wf_laminar_fMRI_func_pRF.coregGM): No edge data
220530-20:27:34,483 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.meanFunc, wf_laminar_fMRI_func_pRF.coregGM): new edge data: {'connect': [('mean_img', 'reference_image')]}


Get intersection of registered GM and manually-defined occipital mask

In [92]:
operation = 'mul'   # ('add' or 'sub' or 'mul' or 'div' or 'rem' or 'max' or
                    # 'min')
                    # operation to perform
                    # flag: -%s, position: 4

In [93]:
occipitalGM = Node(BinaryMaths(operation=operation), name='occipitalGM')

220530-20:27:34,499 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [94]:
wf.connect([(coregGM,occipitalGM,[('output_image', 'in_file')])]) 
wf.connect([(datasourceManualEdits,occipitalGM,[('occipital', 'operand_file')])]) 

220530-20:27:34,507 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.coregGM, wf_laminar_fMRI_func_pRF.occipitalGM): No edge data
220530-20:27:34,508 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.coregGM, wf_laminar_fMRI_func_pRF.occipitalGM): new edge data: {'connect': [('output_image', 'in_file')]}
220530-20:27:34,508 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasourceManualEdits, wf_laminar_fMRI_func_pRF.occipitalGM): No edge data
220530-20:27:34,509 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.datasourceManualEdits, wf_laminar_fMRI_func_pRF.occipitalGM): new edge data: {'connect': [('occipital', 'operand_file')]}


### Put data in sink

A workflow working directory is like a cache. It contains not only the outputs of various processing stages, it also contains various extraneous information such as execution reports, hashfiles determining the input state of processes. All of this is embedded in a hierarchical structure that reflects the iterables that have been used in the workflow. This makes navigating the working directory a not so pleasant experience. And typically the user is interested in preserving only a small percentage of these outputs. The DataSink interface can be used to extract components from this cache and store it at a different location.

In [95]:
dataSink = Node(DataSink(), name='dataSink')
dataSink.inputs.base_directory = out_dir

In [96]:
# T1.nii
wf.connect([(convertT1ToNii,dataSink,[('out_file','func.anat')])])

# realigned func volumes (within and between session)
wf.connect([(applyRealign,dataSink,[('out_file','func.realign')])])

# prepared fieldmap
wf.connect([(prepFieldMap,dataSink,[('out_fieldmap','func.prepFieldMap')])])

# unwarped func volumes
if unwarp:
    wf.connect([(unwarping,dataSink,[('unwarped_file','func.unwarp')])])

# slice-time corrected func volumes
wf.connect([(sliceTimingCorr,dataSink,[('timecorrected_files','func.sliceTimeCorr')])])

# mean functional
wf.connect([(meanFunc,dataSink,[('mean_img','func.meanFunc')])])

# coregistered T1 and transformation matrices
if coreg_method == 'antsRegistration':
    wf.connect([(coreg,dataSink,[('warped_image','func.coreg')])])
    wf.connect([(coreg, dataSink,[('forward_transforms', 'func.forwardTransform')])]) 
    wf.connect([(coreg, dataSink,[('reverse_transforms', 'func.reverseTransform')])]) 
elif coreg_method == 'itk-snap':
    wf.connect([(coreg,dataSink,[('output_image','func.coreg')])])
    
# occipital GM mask for pRF mapping
wf.connect([(occipitalGM,dataSink,[('out_file','func.occipitalGM')])])
    
#if coreg_method == 'flirt':
#    wf.connect([(coreg,dataSink,[('out_file','func.coreg')])])
#    wf.connect([(coreg,dataSink,[('out_matrix_file','func.coreg.@out_matrix_file')])])
#elif coreg_method == 'freesurfer':
#    wf.connect([(coreg,dataSink,[('out_file','func.coreg')])])
#    wf.connect([(coreg,dataSink,[('out_matrix_file','func.coreg.@out_matrix_file')])])
#elif coreg_method == 'antsRegistration':
#    wf.connect([(coreg,dataSink,[('warped_image','func.coreg')])])


220530-20:27:34,525 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.convertT1ToNii, wf_laminar_fMRI_func_pRF.dataSink): No edge data
220530-20:27:34,526 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.convertT1ToNii, wf_laminar_fMRI_func_pRF.dataSink): new edge data: {'connect': [('out_file', 'func.anat')]}
220530-20:27:34,526 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.applyRealign, wf_laminar_fMRI_func_pRF.dataSink): No edge data
220530-20:27:34,527 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.applyRealign, wf_laminar_fMRI_func_pRF.dataSink): new edge data: {'connect': [('out_file', 'func.realign')]}
220530-20:27:34,527 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.prepFieldMap, wf_laminar_fMRI_func_pRF.dataSink): No edge data
220530-20:27:34,528 nipype.workflow DEBUG:
	 (wf_laminar_fMRI_func_pRF.prepFieldMap, wf_laminar_fMRI_func_pRF.dataSink): new edge data: {'connect': [('out_fieldmap', 'func.prepFieldMap')]}
220530-20:27:34,528 nipype.workflow DEBUG:
	 (wf

### Write graph for visualization and run pipeline

In [97]:
if write_graph:
    wf.write_graph("workflowgraph.dot",graph2use='exec', format='svg', simple_form=True)

220530-20:27:34,539 nipype.workflow DEBUG:
	 Creating flat graph for workflow: wf_laminar_fMRI_func_pRF
220530-20:27:34,550 nipype.workflow DEBUG:
	 expanding workflow: wf_laminar_fMRI_func_pRF
220530-20:27:34,552 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.subjects
220530-20:27:34,554 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.datasource
220530-20:27:34,554 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.convertT1ToNii
220530-20:27:34,554 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.datasourceFunc
220530-20:27:34,555 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.sessions
220530-20:27:34,555 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.datasourceManualEdits
220530-20:27:34,555 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.betMagnImg
220530-20:27:34,555 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.acquisitionParams


220530-20:27:34,615 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_id = task-pol_run-02
220530-20:27:34,616 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nr = 3
220530-20:27:34,616 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nvol = 254
220530-20:27:34,616 nipype.workflow DEBUG:
	 Parameterization: paramstr=_sess_id_task-pol_run-02_sess_nr_3_sess_nvol_254
220530-20:27:34,621 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_id = task-ecc_run-01
220530-20:27:34,622 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nr = 4
220530-20:27:34,622 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nvol = 131
220530-20:27:34,622 nipype.workflow DEBUG:
	 Parameterization: paramstr=_sess_id_task-ecc_run-01_sess_nr_4_sess_nvol_131
220530-20:27:34,628 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_id = task-ecc_run-02
220530-20:27:34,628 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nr 

220530-20:27:34,647 nipype.workflow DEBUG:
	 Connected the join node wf_laminar_fMRI_func_pRF.concatenateFunc subgraph to the expanded join point wf_laminar_fMRI_func_pRF.sliceTimingCorr
220530-20:27:34,648 nipype.workflow DEBUG:
	 Qualified the wf_laminar_fMRI_func_pRF.sliceTimingCorr -> wf_laminar_fMRI_func_pRF.concatenateFunc join field in_files as in_filesJ6.
220530-20:27:34,648 nipype.workflow DEBUG:
	 Connected the join node wf_laminar_fMRI_func_pRF.concatenateFunc subgraph to the expanded join point wf_laminar_fMRI_func_pRF.sliceTimingCorr
220530-20:27:34,648 nipype.workflow DEBUG:
	 Qualified the wf_laminar_fMRI_func_pRF.sliceTimingCorr -> wf_laminar_fMRI_func_pRF.concatenateFunc join field in_files as in_filesJ7.
220530-20:27:34,649 nipype.workflow DEBUG:
	 Connected the join node wf_laminar_fMRI_func_pRF.concatenateFunc subgraph to the expanded join point wf_laminar_fMRI_func_pRF.sliceTimingCorr
220530-20:27:34,650 nipype.workflow DEBUG:
	 PE: expanding iterables ... done
220

In [ ]:
if run_pipeline:
    if n_procs == 1:
        wf.run()
    else:
        wf.run('MultiProc', plugin_args={'n_procs': n_procs})

220530-20:27:35,971 nipype.workflow DEBUG:
	 [MultiProc] Starting (n_procs=20, mem_gb=338.94, cwd=/home/mayaaj90/scripts)
220530-20:27:36,149 nipype.workflow DEBUG:
	 Creating flat graph for workflow: wf_laminar_fMRI_func_pRF
220530-20:27:36,161 nipype.workflow DEBUG:
	 expanding workflow: wf_laminar_fMRI_func_pRF
220530-20:27:36,162 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.subjects
220530-20:27:36,162 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.datasource
220530-20:27:36,163 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.convertT1ToNii
220530-20:27:36,163 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.datasourceFunc
220530-20:27:36,163 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.sessions
220530-20:27:36,164 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_func_pRF.datasourceManualEdits
220530-20:27:36,164 nipype.workflow DEBUG:
	 processing node: wf_laminar_fMRI_fun

220530-20:27:36,216 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nvol = 254
220530-20:27:36,216 nipype.workflow DEBUG:
	 Parameterization: paramstr=_sess_id_task-pol_run-01_sess_nr_2_sess_nvol_254
220530-20:27:36,221 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_id = task-pol_run-02
220530-20:27:36,221 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nr = 3
220530-20:27:36,222 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nvol = 254
220530-20:27:36,222 nipype.workflow DEBUG:
	 Parameterization: paramstr=_sess_id_task-pol_run-02_sess_nr_3_sess_nvol_254
220530-20:27:36,227 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_id = task-ecc_run-01
220530-20:27:36,227 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nr = 4
220530-20:27:36,227 nipype.workflow DEBUG:
	 [Node] sessions - setting input sess_nvol = 131
220530-20:27:36,228 nipype.workflow DEBUG:
	 Parameterization: paramstr=_sess_id_task-ecc_run-0

220530-20:27:36,256 nipype.workflow DEBUG:
	 Qualified the wf_laminar_fMRI_func_pRF.sliceTimingCorr -> wf_laminar_fMRI_func_pRF.concatenateFunc join field in_files as in_filesJ5.
220530-20:27:36,257 nipype.workflow DEBUG:
	 Connected the join node wf_laminar_fMRI_func_pRF.concatenateFunc subgraph to the expanded join point wf_laminar_fMRI_func_pRF.sliceTimingCorr
220530-20:27:36,257 nipype.workflow DEBUG:
	 Qualified the wf_laminar_fMRI_func_pRF.sliceTimingCorr -> wf_laminar_fMRI_func_pRF.concatenateFunc join field in_files as in_filesJ6.
220530-20:27:36,257 nipype.workflow DEBUG:
	 Connected the join node wf_laminar_fMRI_func_pRF.concatenateFunc subgraph to the expanded join point wf_laminar_fMRI_func_pRF.sliceTimingCorr
220530-20:27:36,258 nipype.workflow DEBUG:
	 Qualified the wf_laminar_fMRI_func_pRF.sliceTimingCorr -> wf_laminar_fMRI_func_pRF.concatenateFunc join field in_files as in_filesJ7.
220530-20:27:36,258 nipype.workflow DEBUG:
	 Connected the join node wf_laminar_fMRI_func

220530-20:27:38,639 nipype.workflow DEBUG:
	 Tasks currently running: 0. Pending: 0.
220530-20:27:38,640 nipype.workflow INFO:
	 [MultiProc] Running 0 tasks, and 9 jobs ready. Free memory (GB): 338.94/338.94, Free processors: 20/20.
220530-20:27:38,769 nipype.workflow DEBUG:
	 Allocating wf_laminar_fMRI_func_pRF.datasourceFunc ID=0 (0.20GB, 1 threads). Free: 338.74GB, 19 threads.
220530-20:27:38,775 nipype.workflow DEBUG:
	 [Node] Hashes: [('base_directory', '/scratch/mayaaj90/7T-ret'), ('drop_blank_outputs', False), ('field_template', [('sess_id', 'raw/%s/func/%s.nii')]), ('raise_on_empty', True), ('sess_id', 'rest_run-01'), ('sort_filelist', False), ('subject_id', 'sub-01'), ('template', '*'), ('template_args', [('sess_id', [['subject_id', 'sess_id']])])], 5d246c141cf1b79eaa7b019770cf8fdd, /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_sess_id_rest_run-01_sess_nr_6_sess_nvol_50/_subject_id_sub-01/datasourceFunc/_0x5d246c141cf1b79eaa7b019770cf8fdd.json, ['/scratch/maya

220530-20:27:38,883 nipype.workflow DEBUG:
	 [Node] Up-to-date cache found for "wf_laminar_fMRI_func_pRF.datasourceFunc".
220530-20:27:38,883 nipype.workflow DEBUG:
	 Checking hash "wf_laminar_fMRI_func_pRF.datasourceFunc" locally: cached=True, updated=True.
220530-20:27:38,885 nipype.workflow DEBUG:
	 [MultiProc] Submitted task wf_laminar_fMRI_func_pRF.datasourceFunc (taskid=6).
220530-20:27:38,886 nipype.workflow DEBUG:
	 Allocating wf_laminar_fMRI_func_pRF.datasourceFunc ID=18 (0.20GB, 1 threads). Free: 337.54GB, 13 threads.
220530-20:27:38,887 nipype.workflow INFO:
	 [Node] Setting-up "wf_laminar_fMRI_func_pRF.datasourceFunc" in "/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_sess_id_task-bar_run-02_sess_nr_1_sess_nvol_124/_subject_id_sub-01/datasourceFunc".220530-20:27:38,889 nipype.workflow DEBUG:
	 [Node] Hashes: [('base_directory', '/scratch/mayaaj90/7T-ret'), ('drop_blank_outputs', False), ('field_template', [('sess_id', 'raw/%s/func/%s.nii')]), ('raise_on_empt

...

220530-20:29:43,258 nipype.workflow DEBUG:
	 [Node] Hashes: [('function_str', 'def copy_transforms(subject_id,sess_id,sess_nr,sess_nvol,mat_files,working_dir):\n    from os.path import join as opj\n    import shutil\n    import os\n\n    transformMatDir = opj(working_dir,\'_subject_id_\'+subject_id,\n                         \'_sess_id_\'+sess_id+\'_sess_nr_\'+str(sess_nr)+\'_sess_nvol_\'+str(sess_nvol),\n                         \'transformMats\')\n\n    if not os.path.isdir(transformMatDir):\n        os.mkdir(transformMatDir)\n\n    for mat in mat_files:\n        print(\'%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%\')\n        print(mat)\n        print(\'%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%%\')\n\n        # copy file\n        shutil.copy(mat, transformMatDir)\n\n        # remove .mat extension (this is how the ApplyXfm4D interface likes it)\n        base=os.path.basename(mat)\n        filename=os.path.splitext(base)[0]\n        shutil.move(opj(transformMatDir,filename+\'.mat

220530-20:29:43,259 nipype.workflow DEBUG:
	 [Node] Up-to-date cache found for "wf_laminar_fMRI_func_pRF.copyTransforms".
220530-20:29:43,260 nipype.workflow DEBUG:
	 Checking hash "wf_laminar_fMRI_func_pRF.copyTransforms" locally: cached=True, updated=True.
220530-20:29:43,260 nipype.workflow DEBUG:
	 Skipping cached node wf_laminar_fMRI_func_pRF.copyTransforms with ID 55.
220530-20:29:43,260 nipype.workflow INFO:
	 [Job 55] Cached (wf_laminar_fMRI_func_pRF.copyTransforms).
220530-20:29:44,903 nipype.workflow DEBUG:
	 Progress: 1116 jobs, 1101/0/1 (done/running/ready), 0/15 (pending_tasks/waiting).
220530-20:29:44,904 nipype.workflow DEBUG:
	 Tasks currently running: 0. Pending: 0.
220530-20:29:45,14 nipype.workflow DEBUG:
	 Allocating wf_laminar_fMRI_func_pRF.applyRealign ID=56 (0.20GB, 1 threads). Free: 338.74GB, 19 threads.
220530-20:29:45,18 nipype.workflow DEBUG:
	 [Node] Setting 4 connected inputs of node "applyRealign" from 2 previous nodes.
220530-20:29:45,18 nipype.utils DEBU

220530-20:29:49,53 nipype.workflow DEBUG:
	 Resolving paths in outputs loaded from results file.
220530-20:29:49,54 nipype.workflow DEBUG:
	 output: timecorrected_files
220530-20:29:49,54 nipype.workflow DEBUG:
	 [Node] concatenateFunc - setting input in_filesJ1 = /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/_sess_id_task-bar_run-01_sess_nr_0_sess_nvol_124/sliceTimingCorr/atask-bar_run-01_roi_warp4D.nii
220530-20:29:49,55 nipype.utils DEBUG:
	 Loading pkl: /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/_sess_id_task-bar_run-02_sess_nr_1_sess_nvol_124/sliceTimingCorr/result_sliceTimingCorr.pklz
220530-20:29:49,61 nipype.workflow DEBUG:
	 Resolving paths in outputs loaded from results file.
220530-20:29:49,62 nipype.workflow DEBUG:
	 output: timecorrected_files
220530-20:29:49,62 nipype.workflow DEBUG:
	 [Node] concatenateFunc - setting input in_filesJ2 = /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_s

220530-20:29:51,105 nipype.workflow DEBUG:
	 [Node] Up-to-date cache found for "wf_laminar_fMRI_func_pRF.meanFunc".
220530-20:29:51,105 nipype.workflow DEBUG:
	 Checking hash "wf_laminar_fMRI_func_pRF.meanFunc" locally: cached=True, updated=True.
220530-20:29:51,105 nipype.workflow DEBUG:
	 Skipping cached node wf_laminar_fMRI_func_pRF.meanFunc with ID 59.
220530-20:29:51,105 nipype.workflow INFO:
	 [Job 59] Cached (wf_laminar_fMRI_func_pRF.meanFunc).
220530-20:29:52,923 nipype.workflow DEBUG:
	 Progress: 1116 jobs, 1105/0/1 (done/running/ready), 0/11 (pending_tasks/waiting).
220530-20:29:52,924 nipype.workflow DEBUG:
	 Tasks currently running: 0. Pending: 0.
220530-20:29:53,34 nipype.workflow DEBUG:
	 Allocating wf_laminar_fMRI_func_pRF.binarizeMeanFunc ID=60 (0.20GB, 1 threads). Free: 338.74GB, 19 threads.
220530-20:29:53,38 nipype.workflow DEBUG:
	 [Node] Setting 1 connected inputs of node "binarizeMeanFunc" from 1 previous nodes.
220530-20:29:53,39 nipype.utils DEBUG:
	 Loading pkl

220530-20:29:55,82 nipype.workflow DEBUG:
	 [Node] No hashfiles found in "/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/coreg".
220530-20:29:55,82 nipype.workflow DEBUG:
	 Checking hash "wf_laminar_fMRI_func_pRF.coreg" locally: cached=False, updated=False.
220530-20:29:55,85 nipype.workflow DEBUG:
	 [MultiProc] Submitted task wf_laminar_fMRI_func_pRF.coreg (taskid=10).
220530-20:29:55,89 nipype.workflow INFO:
	 [Node] Setting-up "wf_laminar_fMRI_func_pRF.coreg" in "/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/coreg".
220530-20:29:55,100 nipype.workflow DEBUG:
	 [Node] Hashes: [('collapse_output_transforms', True), ('convergence_threshold', ['0.0000010000', '0.0000010000']), ('convergence_window_size', [10, 5]), ('dimension', 3), ('fixed_image', [('/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/meanFunc/merged_func_mcf.nii_mean_reg.nii', 'bd4e443c9cfd1b0936221627b8b47c9a')]), ('fixed

In [ ]:
#mris_verts_registered_tkreg = bbregister_matrix * mris_verts_tkreg

In [ ]:


#!tree "{der_dir}/wf_laminar_fMRI_func_pRF" -I '*js|*json|*pklz|_report|*dot|*html|*txt|*.m'



In [ ]:
#sess_nr = 0
#f"MAT_000{sess_nr}_MAT_"

In [ ]:
#mat_files = [opj(der_dir,wf_name,'test','file1'),
#            opj(der_dir,wf_name,'test','file2'),
#            opj(der_dir,wf_name,'test','file3'),
#            opj(der_dir,wf_name,'test','file4')]
#dest = opj(der_dir,wf_name,'test','test_dest')

In [ ]:
#mat_files
#dest

In [ ]:
#import shutil
#
#for mat in mat_files:
#        shutil.copy(mat, dest)

In [ ]:
#motionOutliers = Node(fsl.MotionOutliers(dummy=n_dummy), name="motionOutliers")

In [ ]:
#sweeps = np.array([-1,0,90,180,270,-1]) # in degrees, -1 is blank
#bar = simulate_bar_stimulus(100, 100, 40, 20, sweeps, 30, 30, 10)
#bar.shape # (100, 100, 180)

#### Save slice-times in file

In [ ]:
def write_st_2file(slice_timing):
    import pickle
    import os
    from os.path import join as opj
    
    filename = 'slice_timing.txt'
    textfile = open(filename, 'w')
    for element in slice_timing:
        textfile.write(str(element) + ' ')
    textfile.close()

    filename = '@'+opj(os.getcwd(),filename)
    
    return filename

In [ ]:
#writeSliceTimes = Node(Function(input_names = ['slice_timing'],
#                              output_names=['filename'],
#                              function=write_st_2file),
#                     name='writeSliceTimes')

In [ ]:
#wf.connect([(acquisitionParams,writeSliceTimes,[('slice_timing','slice_timing')])])

#### Deal with obliquity

Otherwise, next step throws a warning:
If you are performing spatial transformations on an oblique dset, 
  such as /scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/_sess_id_rest_run-01_sess_nr_6_sess_nvol_50/sliceTimingCorr/rest_run-01_roi_warp4D_unwarped.nii,
  or viewing/combining it with volumes of differing obliquity,
  you should consider running: 
     3dWarp -deoblique 
  on this and  other oblique datasets in the same session.
 See 3dWarp -help for details.
++ Oblique dataset:/scratch/mayaaj90/7T-ret/derivatives/wf_laminar_fMRI_func_pRF/_subject_id_sub-01/_sess_id_rest_run-01_sess_nr_6_sess_nvol_50/sliceTimingCorr/rest_run-01_roi_warp4D_unwarped.nii is 12.360637 degrees from plumb.

https://nipype.readthedocs.io/en/0.12.1/interfaces/generated/nipype.interfaces.afni.preprocess.html#warp

In [ ]:
#deoblique = True                  # (a boolean)
#                                  # transform dataset from oblique to cardinal
#                                  # flag: -deoblique

In [ ]:
#deoblique = Node(Warp(deoblique=deoblique),name='deoblique')

###### wf.connect([(unwarp,deoblique,[('unwarped_file','in_file')])])